# 1.0 General Overview

The base model for food classification of this dataset has achieved a top 5 accuracy of 98.3% and top 1 accuracy of 88.95%. In this project, we will attempt to improve on the top 1 accuracy score. However, the dataset used for this project does not belong to me and is not publicly available. 

Prior to the building of the model below in attempt to improve on the performance of the base model, this section will delineate the approach adopted by the base model, and the approach adopted to improve on the base model.

#### Base Model Approach
Architecture: A ResNet18 model pre-trained on ImageNet  
Loss: Cross Entropy Loss  
Optimizer for Cross Entropy Loss: SGD with 0.9 Momentum and Learning Rate of 0.001 with Learning Rate Scheduler of gamma 0.1 at steps = 20  

#### Improved Model Apporach
Architecture: A ResNet18 model pre-trained on ImageNet followed by fine-tuning on an external Food101 dataset  
Loss: Cross Entropy Loss and Contrastive-Center Loss  
Optimizer for Cross Entropy Loss: SGD with 0.9 Momentum and Learning Rate of 0.001 with Learning Rate Scheduler of gamma 0.1 at steps = 20  
Optimizer for Contrastive-Center Loss: Adagrad with learning rate of 0.001  

Therefore, the novelty introduced are the addition of a contrastive-center loss and the fine-tuning of the base model on an external dataset - Food101 Dataset.

# 2.0 Notebook Content

With reference to the above, this notebook will be divided into the following sections:  
1.0 General Overview  
2.0 Notebook Content  
3.0 Discussion on Fine-Tuning Model on External Food101 Dataset  
4.0 Discussion on Contrastive-Center Loss  
5.0 Discussion on the Implementation of Proposed Novelties  
6.0 Loading Packages   
7.0 Changing ResNet18 Source Code to Obtain Deep Features Prior to Softmax Activation  
8.0 Data Transformation Function  
9.0 Data Loading Function  
10.0 Model Loading Function  
11.0 Defining Contrastive Center Loss Function  
12.0 Model Training  
13.0 Discussion on Results  
14.0 References

# 3.0 Discussion on Fine-Tuning Model on External Food101 Dataset

According to Cui et al [1], although large scale image datasets such as ImageNet contains a large amount of data, these images are typically generic and "contain objects in the center with similar scale and simple backgrounds". Additionally, the authors of the paper discovered that datasets are often biased in terms of their content and style, which might affect the performance of transfer learning on another dataset that contains images that differs significantly. Consequently, the authors managed to achieved better transfer learning by fine-tuning the networks trained on selected subsets of data based on the paper's proposed measure to estimate domain similarity.

Motivated by the proposed methods in the paper, an attempt was made to fine-tune the model based on a dataset similar to Food59 prior to training end-to-end on the Food59 dataset. Based on the paper by Bossard, L. et al [2], a challenging dataset with 101 food categories with a total of 101,000 images, where each class has 750 training images and 250 test images, was introduced. Similar to the Food59 dataset, the images in the Food101 dataset contained noises in the data that is common across food images. 

Therefore, based on the discussion above, our model was first fine-tuned on the Food101 dataset prior to conducting end-to-end training on the Food59 dataset in hope of achieving better results.

# 4.0 Discussion on Contrastive-Center Loss

One of the challenges in visual classification and recognition task is to obtain more discriminative features to improve the performance of the deep neural networks. One strategy implemented by various papers are the introduction of contrastive loss [4], which is a distance-based loss function that penalises on the distance between semantically similar examples, as well as the introduction of center loss [5], which learns a center for the deep features of each class and penalizes the distances between the deep features and their corresponding class centers.

Following the introduction of the two losses above, according to Qi, C. & Su, F. [3], the proposed contrastive-center loss was proposed to "consider intra-class compactness and inter-class separability, by penalizing the contrastive values between: (1) the distances of training samples to their corresponding class centers, and (2) the sum of the distances of training samples to their non-corresponding class centers." Discriminative features within the same class should therefore have low separability while discriminative features of different classes should have high separability.

In this case, the contrastive-center loss was proposed to not only consider inter-class variability, but also to consider intra-class variability.

# 5.0 Discussion on Implementation of Proposed Novelties

Based on section 3.0 above, the fine-tuning of the ResNet18 model on the external Food101 dataset can be referred to in the Jupyter Notebook named "Fine-Tuning on Food101". The weights saved on the fine tuned model is named "50epochs_food101_best_top1_val_model.ft", and is loaded in our model in section 10.0 below.

Based on section 4.0 above, since the contrastive-center loss has to learn a center for the deep features of each class, it is necessary that we first edit the source code of the ResNet18 model such that it allows the return of the number of deep features (which is 512) prior to passing through the softmax layer for classification. The editing of the ResNet18 source code in in section 7.0 below. 

# 6.0 Loading Packages

Before we proceed, we will first load the necessary packages

In [2]:
# %load train.py
from __future__ import print_function, division

import torch
import argparse
import json 
import torch.nn as nn
import torch.optim as optim
from torch.optim import lr_scheduler
import numpy as np
import torchvision
from torchvision import datasets, models, transforms
from functools import partial 
import time
import os
import random
import copy
import pdb 
from tqdm import tqdm
from utils import * 
from torch.autograd import Variable
from torch.autograd.function import Function

import math
from torch.optim import Optimizer

# 7.0 Changing ResNet18 Source Code to Obtain Deep Features Prior to Softmax Activation  

In this section, we will have to edit the source code for pytorch ResNet18 model in order for us to derive the deep discriminative features prior to the final softmax layer for the formulation of the contrastive-center loss. In particular, the edited lines are under the forward define function in the ResNet Class, which are commented for clearer indication of the changes from the original code to the revised code.

In [3]:
import torch.nn as nn
import torch.utils.model_zoo as model_zoo


__all__ = ['ResNet', 'resnet18', 'resnet34', 'resnet50', 'resnet101',
           'resnet152']


model_urls = {
    'resnet18': 'https://download.pytorch.org/models/resnet18-5c106cde.pth',
    'resnet34': 'https://download.pytorch.org/models/resnet34-333f7ec4.pth',
    'resnet50': 'https://download.pytorch.org/models/resnet50-19c8e357.pth',
    'resnet101': 'https://download.pytorch.org/models/resnet101-5d3b4d8f.pth',
    'resnet152': 'https://download.pytorch.org/models/resnet152-b121ed2d.pth',
}


def conv3x3(in_planes, out_planes, stride=1):
    """3x3 convolution with padding"""
    return nn.Conv2d(in_planes, out_planes, kernel_size=3, stride=stride,
                     padding=1, bias=False)


def conv1x1(in_planes, out_planes, stride=1):
    """1x1 convolution"""
    return nn.Conv2d(in_planes, out_planes, kernel_size=1, stride=stride, bias=False)


class BasicBlock(nn.Module):
    expansion = 1

    def __init__(self, inplanes, planes, stride=1, downsample=None):
        super(BasicBlock, self).__init__()
        self.conv1 = conv3x3(inplanes, planes, stride)
        self.bn1 = nn.BatchNorm2d(planes)
        self.relu = nn.ReLU(inplace=True)
        self.conv2 = conv3x3(planes, planes)
        self.bn2 = nn.BatchNorm2d(planes)
        self.downsample = downsample
        self.stride = stride

    def forward(self, x):
        identity = x

        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)

        out = self.conv2(out)
        out = self.bn2(out)

        if self.downsample is not None:
            identity = self.downsample(x)

        out += identity
        out = self.relu(out)

        return out


class Bottleneck(nn.Module):
    expansion = 4

    def __init__(self, inplanes, planes, stride=1, downsample=None):
        super(Bottleneck, self).__init__()
        self.conv1 = conv1x1(inplanes, planes)
        self.bn1 = nn.BatchNorm2d(planes)
        self.conv2 = conv3x3(planes, planes, stride)
        self.bn2 = nn.BatchNorm2d(planes)
        self.conv3 = conv1x1(planes, planes * self.expansion)
        self.bn3 = nn.BatchNorm2d(planes * self.expansion)
        self.relu = nn.ReLU(inplace=True)
        self.downsample = downsample
        self.stride = stride

    def forward(self, x):
        identity = x

        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)

        out = self.conv2(out)
        out = self.bn2(out)
        out = self.relu(out)

        out = self.conv3(out)
        out = self.bn3(out)

        if self.downsample is not None:
            identity = self.downsample(x)

        out += identity
        out = self.relu(out)

        return out


class ResNet(nn.Module):

    def __init__(self, block, layers, num_classes=1000, zero_init_residual=False):
        super(ResNet, self).__init__()
        self.inplanes = 64
        self.conv1 = nn.Conv2d(3, 64, kernel_size=7, stride=2, padding=3,
                               bias=False)
        self.bn1 = nn.BatchNorm2d(64)
        self.relu = nn.ReLU(inplace=True)
        self.maxpool = nn.MaxPool2d(kernel_size=3, stride=2, padding=1)
        self.layer1 = self._make_layer(block, 64, layers[0])
        self.layer2 = self._make_layer(block, 128, layers[1], stride=2)
        self.layer3 = self._make_layer(block, 256, layers[2], stride=2)
        self.layer4 = self._make_layer(block, 512, layers[3], stride=2)
        self.avgpool = nn.AdaptiveAvgPool2d((1, 1))
        self.fc = nn.Linear(512 * block.expansion, num_classes)

        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
            elif isinstance(m, nn.BatchNorm2d):
                nn.init.constant_(m.weight, 1)
                nn.init.constant_(m.bias, 0)

        # Zero-initialize the last BN in each residual branch,
        # so that the residual branch starts with zeros, and each residual block behaves like an identity.
        # This improves the model by 0.2~0.3% according to https://arxiv.org/abs/1706.02677
        if zero_init_residual:
            for m in self.modules():
                if isinstance(m, Bottleneck):
                    nn.init.constant_(m.bn3.weight, 0)
                elif isinstance(m, BasicBlock):
                    nn.init.constant_(m.bn2.weight, 0)

    def _make_layer(self, block, planes, blocks, stride=1):
        downsample = None
        if stride != 1 or self.inplanes != planes * block.expansion:
            downsample = nn.Sequential(
                conv1x1(self.inplanes, planes * block.expansion, stride),
                nn.BatchNorm2d(planes * block.expansion),
            )

        layers = []
        layers.append(block(self.inplanes, planes, stride, downsample))
        self.inplanes = planes * block.expansion
        for _ in range(1, blocks):
            layers.append(block(self.inplanes, planes))

        return nn.Sequential(*layers)

    def forward(self, x):
        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        x = self.maxpool(x)

        x = self.layer1(x)
        x = self.layer2(x)
        x = self.layer3(x)
        #x = self.layer4(x)         <--- Start of Original Source Code Commented Out

        #x = self.avgpool(x)
        #x = x.view(x.size(0), -1)
        #x = self.fc(x)
        
        #return x                   <--- End of Original Source Code Commented Out

        # To save pre-final layer's features

        feat = self.avgpool(self.layer4(x))  # <--- Start of Newly Edited Code
        feat = feat.view(feat.size(0), -1)
        x = self.fc(feat)
        
        return feat, x                       # <--- End of New Edited Code


def resnet18(pretrained=False, **kwargs):
    """Constructs a ResNet-18 model.

    Args:
        pretrained (bool): If True, returns a model pre-trained on ImageNet
    """
    model = ResNet(BasicBlock, [2, 2, 2, 2], **kwargs)
    if pretrained:
        model.load_state_dict(model_zoo.load_url(model_urls['resnet18']))
    return model

# 8.0 Data Transformation Function  

In this section, we perform data augmentation for both our training and test data. However, no changes were made with reference to the base model. The same data augmentation was used.

In [4]:
def transfrom_data():
    data_transforms = {
    'train': transforms.Compose([
        transforms.RandomResizedCrop(224),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor(), 
        transforms.Normalize(mean=[0.485, 0.456, 0.406],
                            std=[0.229, 0.224, 0.225])
        ]),
    'val': transforms.Compose([
        transforms.Resize(256),
        transforms.CenterCrop(224),
        transforms.ToTensor(), 
        transforms.Normalize(mean=[0.485, 0.456, 0.406],
                            std=[0.229, 0.224, 0.225])
        ])
    }

    return data_transforms

# 9.0 Data Loading Function  

In this section, we define a function to load our data. Similar to section 8.0 above, no changes were made to this function.

In [5]:
def load_data(batch_size, num_workers):
    print("Start loading data")
    data_dir = '../'
    image_datasets = {x: datasets.ImageFolder(os.path.join(data_dir, x), transfrom_data()[x]) for x in ['train', 'val']}
    dataloaders = {x: torch.utils.data.DataLoader(image_datasets[x], batch_size=batch_size, shuffle=True, num_workers=num_workers) \
                    for x in ['train', 'val']}
    class_names = image_datasets['train'].classes
    dataset_sizes = {x: len(image_datasets[x]) for x in ['train', 'val']}
    print("Dataset sizes: Train {} Val {}".format(dataset_sizes['train'], dataset_sizes['val']))
    print("Number of classes: Train {} Val {}".format(len(image_datasets['train'].classes), len(image_datasets['val'].classes)))

    return dataloaders, class_names, dataset_sizes

# 10.0 Model Loading Function  

In this section, we will define our model loading function, which differs from the base model's function. The following delineates the changes to the function:  
#### 1. Loading Saved Weights  
Since we are loading our saved weights from the model that was fine-tuned on the external Food101 data, we have to first load the saved weights that was named "50epochs_food101_best_top1_val_model.ft".  
#### 2. Creating New OrderedDict that Does Not Contain 'Module'  
Since the model that was fine-tuned on the Food101 dataset was trained using nn.DataParallel, which stores the model in module, and since we are not loading it with DataParallel, we have to first create a new ordered dict without the module prefix and load the model back.  
#### 3. Changing Number of Classes in Final FC Layer to 101  
Since the fine-tuned model was trained on the Food101 dataset, which has 101 classes, we have to reconstruct the identical ResNet18 architecture in order to load the saved weights.

In [6]:
def load_model(class_names):
    # Loading Saved Weights from Food101
    state_dict = torch.load('./50epochs_food101_best_top1_val_model.ft')
    
    # create new OrderedDict that does not contain `module.`
    from collections import OrderedDict
    new_state_dict = OrderedDict()
    for k, v in state_dict.items():
        name = k[7:] # remove `module.`
        new_state_dict[name] = v
    
    model = resnet18(pretrained=False)
    num_ftrs = model.fc.in_features
    model.fc = nn.Linear(num_ftrs, 101)
    model.load_state_dict(new_state_dict)

    return model

# 11.0 Defining Contrastive Center Loss Function  

Formally, the formula of the contrastive-center loss can be seen below:

![Formula for Contrastive-Center Loss](img/contrastive_center_formula.png)

Where Lct−c denotes the contrastive-center loss. m denotes the number of training samples in a min-batch. xi ∈ Rd denotes the ith training sample with feature dimension d. yi denotes the label of xi. cyi ∈ Rd denotes the yith class center of deep features with dimension d. k denotes the number of class. δ is a constant used for preventing the denominator equal to 0.

Therefore, the formula can be defined in the function below:

In [8]:
import torch
import torch.nn as nn
from torch.autograd import Variable
from logzero import logger

class ContrastiveCenterLoss(nn.Module):
    def __init__(self, dim_hidden, num_classes, lambda_c=1.0, use_cuda=True):
        super(ContrastiveCenterLoss, self).__init__()
        self.dim_hidden = dim_hidden
        self.num_classes = num_classes
        self.lambda_c = lambda_c
        self.centers = nn.Parameter(torch.randn(num_classes, dim_hidden))
        self.use_cuda = use_cuda
        
    def forward(self, y, hidden):
        batch_size = hidden.size()[0]
        expanded_centers = self.centers.expand(batch_size, -1, -1)
        expanded_hidden = hidden.expand(self.num_classes, -1, -1).transpose(1, 0)
        distance_centers = (expanded_hidden - expanded_centers).pow(2).sum(dim=-1)
        distances_same = distance_centers.gather(1, y.unsqueeze(1))
        intra_distances = distances_same.sum()
        inter_distances = distance_centers.sum().sub(intra_distances)
        epsilon = 1e-6
        loss = (self.lambda_c / 2.0 / batch_size) * intra_distances / \
               (inter_distances + epsilon) / 0.1
        logger.info('{},{},{}'.format(
            intra_distances.data, inter_distances.data, loss.data))
        return loss

# 12.0 Model Training  

Finally, we will perform our model training below:  

In this case, we define our loss as the Cross Entropy Loss + Contrastive Center Loss, where the optimizer for our Contrastive Center Loss is Adagrad, with learning rate of 0.001.

In [9]:
def train_model(dataloaders, model, dataset_sizes, criterion, optimizer, scheduler, num_epochs, save_dir, f):
    since = time.time()
    
    best_val_top1_acc = 0.0
    best_val_top5_acc = 0.0
    best_top1_val_epoch = -1 
    best_top5_val_epoch = -1
    final_val_top5_acc = 0.0
    final_val_top1_acc = 0.0

    for epoch in range(num_epochs):  # loop over the dataset multiple times
        for phase in ['train', 'val']:
            if phase == 'train':
                scheduler.step()
                model.train()
            else:
                model.eval()

            running_loss = 0.0
            top1_running_corrects = 0
            top5_running_corrects = 0

            it = tqdm(range(len(dataloaders[phase])), desc="Epoch {}/{}, Split {}".format(epoch, num_epochs - 1, phase), ncols=0)
            data_iter = iter(dataloaders[phase])
            for niter in it:
                inputs, labels = data_iter.next()
                inputs = inputs.cuda()
                labels = labels.cuda()

                optimizer[0].zero_grad()
                optimizer[1].zero_grad()
                
                with torch.set_grad_enabled(phase == 'train'):
                    feats, outputs = model(inputs)
                    loss = criterion[0](outputs, labels) + criterion[1](labels, feats)
                    prec1, prec5 = accuracy(outputs, labels, topk=(1,5))

                    if phase == 'train':
                        loss.backward()

                        optimizer[0].step()
                        optimizer[1].step()

                training_loss = loss.item()
                running_loss += loss.item() * inputs.size(0)
                top1_running_corrects += prec1[0]
                top5_running_corrects += prec5[0]

            epoch_loss = running_loss / dataset_sizes[phase]
            top1_epoch_acc = float(top1_running_corrects) / dataset_sizes[phase]
            top5_epoch_acc = float(top5_running_corrects) / dataset_sizes[phase]
            print('{} Epoch Loss: {:.6f} Epoch top1 Acc: {:.6f} Epoch top5 Acc: {:.6f}\n'.format(phase, epoch_loss, top1_epoch_acc, top5_epoch_acc))
            with open(epoch_trace_f_dir, "a") as f:
                lr = optimizer[0].param_groups[0]['lr']
                f.write("{},{},{},{:e},{:e},{:e}\n".format(epoch,phase,lr,epoch_loss,top1_epoch_acc,top5_epoch_acc))

            if phase == 'val' and top1_epoch_acc > best_val_top1_acc:
                print("Top1 val Acc improve from {:6f} --> {:6f}".format(best_val_top1_acc, top1_epoch_acc))
                best_val_top1_acc = top1_epoch_acc
                final_val_top5_acc = top5_epoch_acc
                best_top1_val_epoch = epoch
                save_f_dir = os.path.join(save_dir, "best_top1_val_model.ft")
                print("Saving best top 1 val model into {}...".format(save_f_dir))
                torch.save(model.state_dict(), save_f_dir)
                
            if phase == 'val' and top5_epoch_acc > best_val_top5_acc:
                print("Top5 val Acc improve from {:6f} --> {:6f}".format(best_val_top5_acc, top5_epoch_acc))
                best_val_top5_acc = top5_epoch_acc
                final_val_top1_acc = top1_epoch_acc
                best_top5_val_epoch = epoch
                save_f_dir = os.path.join(save_dir, "best_top5_val_model.ft")
                print("Saving best top 5 val model into {}...".format(save_f_dir))
                torch.save(model.state_dict(), save_f_dir)

        print()

    time_elapsed = time.time() - since
    print('Training complete in {:.0f}m {:.0f}s'.format(time_elapsed // 60, time_elapsed % 60))
    print('Best top1 val Acc: {:6f}'.format(best_val_top1_acc))
    print('Final top5 val Acc: {:6f}'.format(final_val_top5_acc))
    print('Best val top 1 model is saved at epoch # {}'.format(best_top1_val_epoch))
    print('Best val top 5 model is saved at epoch # {}'.format(best_top5_val_epoch))
    
if __name__=="__main__":

    dataloaders, class_names, dataset_sizes = load_data(16, 12)
    model= load_model(class_names)
    model = model.cuda()

    # Losses
    CE_loss = nn.CrossEntropyLoss()                       # <--- Cross Entropy Loss    
    center_loss = ContrastiveCenterLoss(dim_hidden=512,   # <--- Contrastive Center Loss
                                        num_classes=59,
                                        lambda_c=1.0)
    CE_loss, center_loss = CE_loss.cuda(), center_loss.cuda()
    criterion = [CE_loss, center_loss]
    
    # Optimizers & Scheduler
    optimizer_nn = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
    optimizer_c = optim.Adagrad(center_loss.parameters(), lr=0.001)         # <--- Optimizer for Contrastive Center Loss
    
    scheduler = lr_scheduler.StepLR(optimizer_nn, step_size=20, gamma=0.1)
    
    optimizer = [optimizer_nn, optimizer_c]
    
    # Number of Epochs 
    num_epochs = 30
    
    # Saving Results
    save_dir = './outputs/'
    if not os.path.isdir(save_dir):
        os.makedirs(save_dir)
    epoch_trace_f_dir = os.path.join(save_dir, "trace.csv")
    with open(epoch_trace_f_dir, "w") as f:
        f.write("epoch,split,lr,loss,top1_acc,top5_acc\n")

    train_model(dataloaders, model, dataset_sizes, criterion, optimizer, scheduler, num_epochs, save_dir, f)

Start loading data
Dataset sizes: Train 28236 Val 588
Number of classes: Train 59 Val 59


Epoch 0/29, Split train:   0% 0/1765 [00:00<?, ?it/s][I 190320 03:56:30 <ipython-input-8-77b0d945ac8e>:28] 19089.35546875,1116961.5,0.0053407601080834866
Epoch 0/29, Split train:   0% 1/1765 [00:16<8:02:30, 16.41s/it][I 190320 03:56:31 <ipython-input-8-77b0d945ac8e>:28] 19343.015625,1108396.0,0.005453549791127443
Epoch 0/29, Split train:   0% 2/1765 [00:16<5:40:00, 11.57s/it][I 190320 03:56:31 <ipython-input-8-77b0d945ac8e>:28] 19598.681640625,1126104.625,0.005438738036900759
Epoch 0/29, Split train:   0% 3/1765 [00:16<3:59:53,  8.17s/it][I 190320 03:56:31 <ipython-input-8-77b0d945ac8e>:28] 18420.98046875,1091620.0,0.005273406859487295
Epoch 0/29, Split train:   0% 4/1765 [00:17<2:49:48,  5.79s/it][I 190320 03:56:31 <ipython-input-8-77b0d945ac8e>:28] 18808.66796875,1102075.375,0.005333309061825275
Epoch 0/29, Split train:   0% 5/1765 [00:17<2:00:49,  4.12s/it][I 190320 03:56:32 <ipython-input-8-77b0d945ac8e>:28] 18749.81640625,1070208.0,0.005474933423101902
Epoch 0/29, Split train:   0

Epoch 0/29, Split train:   6% 100/1765 [00:40<07:18,  3.80it/s][I 190320 03:56:55 <ipython-input-8-77b0d945ac8e>:28] 18938.45703125,1115594.375,0.005305035971105099
Epoch 0/29, Split train:   6% 101/1765 [00:40<07:49,  3.54it/s][I 190320 03:56:55 <ipython-input-8-77b0d945ac8e>:28] 19123.26953125,1116662.125,0.005351682659238577
Epoch 0/29, Split train:   6% 102/1765 [00:41<07:42,  3.59it/s][I 190320 03:56:55 <ipython-input-8-77b0d945ac8e>:28] 19222.0546875,1114127.25,0.005391567014157772
Epoch 0/29, Split train:   6% 103/1765 [00:41<07:13,  3.83it/s][I 190320 03:56:56 <ipython-input-8-77b0d945ac8e>:28] 18883.359375,1123590.125,0.005251959897577763
Epoch 0/29, Split train:   6% 104/1765 [00:41<07:26,  3.72it/s][I 190320 03:56:56 <ipython-input-8-77b0d945ac8e>:28] 19266.0546875,1102874.5,0.005459045525640249
Epoch 0/29, Split train:   6% 105/1765 [00:41<07:16,  3.80it/s][I 190320 03:56:56 <ipython-input-8-77b0d945ac8e>:28] 19130.359375,1102072.375,0.005424541421234608
Epoch 0/29, Split t

Epoch 0/29, Split train:  11% 199/1765 [01:05<07:24,  3.52it/s][I 190320 03:57:20 <ipython-input-8-77b0d945ac8e>:28] 19720.498046875,1149805.0,0.005359739996492863
Epoch 0/29, Split train:  11% 200/1765 [01:05<06:46,  3.85it/s][I 190320 03:57:20 <ipython-input-8-77b0d945ac8e>:28] 19461.060546875,1153491.125,0.005272326059639454
Epoch 0/29, Split train:  11% 201/1765 [01:05<06:15,  4.17it/s][I 190320 03:57:20 <ipython-input-8-77b0d945ac8e>:28] 19925.318359375,1157241.875,0.005380605347454548
Epoch 0/29, Split train:  11% 202/1765 [01:06<05:55,  4.39it/s][I 190320 03:57:20 <ipython-input-8-77b0d945ac8e>:28] 20510.85546875,1177079.5,0.0054453774355351925
Epoch 0/29, Split train:  12% 203/1765 [01:06<05:41,  4.57it/s][I 190320 03:57:21 <ipython-input-8-77b0d945ac8e>:28] 19464.328125,1138583.0,0.005342256743460894
Epoch 0/29, Split train:  12% 204/1765 [01:06<05:30,  4.72it/s][I 190320 03:57:21 <ipython-input-8-77b0d945ac8e>:28] 19974.76953125,1164010.5,0.0053625935688614845
Epoch 0/29, Spl

Epoch 0/29, Split train:  17% 299/1765 [01:26<05:05,  4.80it/s][I 190320 03:57:41 <ipython-input-8-77b0d945ac8e>:28] 19519.01953125,1163848.25,0.0052409702911973
Epoch 0/29, Split train:  17% 300/1765 [01:26<05:05,  4.80it/s][I 190320 03:57:41 <ipython-input-8-77b0d945ac8e>:28] 20065.888671875,1159185.375,0.005409480072557926
Epoch 0/29, Split train:  17% 301/1765 [01:26<05:00,  4.86it/s][I 190320 03:57:41 <ipython-input-8-77b0d945ac8e>:28] 20244.41015625,1175289.125,0.00538282748311758
Epoch 0/29, Split train:  17% 302/1765 [01:27<05:00,  4.87it/s][I 190320 03:57:41 <ipython-input-8-77b0d945ac8e>:28] 19991.177734375,1181553.0,0.005287314765155315
Epoch 0/29, Split train:  17% 303/1765 [01:27<05:04,  4.79it/s][I 190320 03:57:42 <ipython-input-8-77b0d945ac8e>:28] 19868.849609375,1159284.875,0.005355901550501585
Epoch 0/29, Split train:  17% 304/1765 [01:27<05:03,  4.81it/s][I 190320 03:57:42 <ipython-input-8-77b0d945ac8e>:28] 20675.33203125,1163021.875,0.0055553908459842205
Epoch 0/29, 

...

Epoch 29/29, Split train:  89% 1569/1765 [09:56<01:11,  2.74it/s][I 190320 07:19:44 <ipython-input-8-77b0d945ac8e>:28] 20199.51171875,1228722.0,0.005137328058481216
Epoch 29/29, Split train:  89% 1570/1765 [09:56<01:11,  2.74it/s][I 190320 07:19:45 <ipython-input-8-77b0d945ac8e>:28] 20598.734375,1258167.75,0.005116253159940243
Epoch 29/29, Split train:  89% 1571/1765 [09:57<01:10,  2.75it/s][I 190320 07:19:45 <ipython-input-8-77b0d945ac8e>:28] 20078.9140625,1256108.625,0.004995316732674837
Epoch 29/29, Split train:  89% 1572/1765 [09:57<01:10,  2.75it/s][I 190320 07:19:46 <ipython-input-8-77b0d945ac8e>:28] 19786.86328125,1255264.75,0.004925969056785107
Epoch 29/29, Split train:  89% 1573/1765 [09:57<01:09,  2.75it/s][I 190320 07:19:46 <ipython-input-8-77b0d945ac8e>:28] 19740.787109375,1222546.0,0.005046023987233639
Epoch 29/29, Split train:  89% 1574/1765 [09:58<01:09,  2.75it/s][I 190320 07:19:46 <ipython-input-8-77b0d945ac8e>:28] 19840.453125,1269281.875,0.004884763620793819
Epoch 29

Epoch 29/29, Split train:  94% 1667/1765 [10:32<00:35,  2.75it/s][I 190320 07:20:21 <ipython-input-8-77b0d945ac8e>:28] 18989.21875,1226548.625,0.00483807222917676
Epoch 29/29, Split train:  95% 1668/1765 [10:32<00:35,  2.73it/s][I 190320 07:20:21 <ipython-input-8-77b0d945ac8e>:28] 19177.30859375,1229275.25,0.004875156097114086
Epoch 29/29, Split train:  95% 1669/1765 [10:33<00:35,  2.72it/s][I 190320 07:20:21 <ipython-input-8-77b0d945ac8e>:28] 18918.296875,1242349.125,0.004758700728416443
Epoch 29/29, Split train:  95% 1670/1765 [10:33<00:34,  2.72it/s][I 190320 07:20:22 <ipython-input-8-77b0d945ac8e>:28] 19078.10546875,1229957.75,0.0048472462221980095
Epoch 29/29, Split train:  95% 1671/1765 [10:33<00:34,  2.73it/s][I 190320 07:20:22 <ipython-input-8-77b0d945ac8e>:28] 18208.283203125,1215609.125,0.0046808538027107716
Epoch 29/29, Split train:  95% 1672/1765 [10:34<00:34,  2.73it/s][I 190320 07:20:22 <ipython-input-8-77b0d945ac8e>:28] 17917.1015625,1224454.25,0.00457272632047534
Epoch 

train Epoch Loss: 0.248285 Epoch top1 Acc: 0.931045 Epoch top5 Acc: 0.987357



Epoch 29/29, Split val:   0% 0/37 [00:00<?, ?it/s][I 190320 07:21:06 <ipython-input-8-77b0d945ac8e>:28] 26707.931640625,1567175.625,0.005325649864971638
Epoch 29/29, Split val:   3% 1/37 [00:09<05:46,  9.62s/it][I 190320 07:21:06 <ipython-input-8-77b0d945ac8e>:28] 24678.01171875,1479295.25,0.005213211290538311
Epoch 29/29, Split val:   5% 2/37 [00:09<03:57,  6.79s/it][I 190320 07:21:06 <ipython-input-8-77b0d945ac8e>:28] 24260.046875,1467721.375,0.005165329668670893
Epoch 29/29, Split val:   8% 3/37 [00:09<02:43,  4.81s/it][I 190320 07:21:06 <ipython-input-8-77b0d945ac8e>:28] 25450.599609375,1486361.625,0.005350859835743904
Epoch 29/29, Split val:  11% 4/37 [00:10<01:52,  3.42s/it][I 190320 07:21:07 <ipython-input-8-77b0d945ac8e>:28] 23709.20703125,1422144.75,0.005209826864302158
Epoch 29/29, Split val:  14% 5/37 [00:10<01:18,  2.44s/it][I 190320 07:21:07 <ipython-input-8-77b0d945ac8e>:28] 26201.197265625,1500621.5,0.005456321872770786
Epoch 29/29, Split val:  16% 6/37 [00:10<00:54,  1.

val Epoch Loss: 0.514728 Epoch top1 Acc: 0.884354 Epoch top5 Acc: 0.974490


Training complete in 204m 57s
Best top1 val Acc: 0.891156
Final top5 val Acc: 0.972789
Best val top 1 model is saved at epoch # 23
Best val top 5 model is saved at epoch # 14


# 13.0 Discussion on Results

Based on the results obtained above, we can see that the best top 1 validation accuracy is 0.891, which is only 0.02 higher than the base model best top 1 validation accuracy of 0.889. 

While there was a slight improvement, it did not exceed expectation. The following paragraphs will delineate the possible reasons for the slight improvement, as well as possible justifications on why the results did not exceed expectations based on the proposed novelties.

#### Fine-Tuning on External Food101 Dataset
Even though the model was fine-tuned on a dataset of a similar domain - food, there could be other factors that prevented the fine-tuned model to generalise well over the Food59 dataset. One possible reason is that the Food59 dataset contains many local food categories that are not common across the Food101 dataset. In particular, the Food59 dataset contains images of food from a fusion of multiple types of cuisine, such as Western and Asian. On the other hand, while the Food101 dataset does contain several classes of food from both Western and Asian cuisine, a much larger proportion of them are Western food categories. 

Additionally, the Food59 dataset contains drinks, such as americano and instant coffee as food classes, while the Food101 dataset does not contain drinks.

However, for future work, it could be possible to tap onto other well-balanced dataset that contains food classes that are similar to that of Food59 for fine-tuning. For example, while searching for datasets that are of a similar domain with Food59, there was another food dataset called the ChineseFoodNet dataset. However, the data was unavailable for download. By integrating several food dataset where the model can be pre-trained or fine-tuned on, it could possibly lead to a better classification result.

#### Application of Contrastive Center Loss
The Contrastive Center Loss was a proposed loss to improve upon other training strategy to obtain more discriminative features. Not only does it consider intra-class compactness, but it also considers inter-class separability. Theoretically, this loss function would be ideal in performing image classification where there are low variability of examples across classes and / or high variability of examples within a class.

In this case, within the Food59 dataset, there are several confusing inter-classes of food. For example, some images of instant coffee looks very similar to images of kopi-o. Furthermore, some images within a class appear to be different as well. For example, within the food class of braised pig skin, there are several food images that do not look like braised pig skin.

As a result, this allows the model to perform better when using contrastive center loss than if only cross-entropy loss is used.

# 14.0 References

[1] Cui, Yin & Song, Yang & Sun, Chen & Howard, Andrew & Belongie, Serge. (2018). Large Scale Fine-Grained Categorization and Domain-Specific Transfer Learning. 4109-4118. 10.1109/CVPR.2018.00432. 

[2] Bossard, L., Guillaumin, M., & Gool, L.V. (2014). Food-101 - Mining Discriminative Components with Random Forests. ECCV.

[3] Qi, C. & Su, F. (2017) Contrastive-Center Loss For Deep Neural Networks. 2017 IEEE International Conference on Image Processing (ICIP), Beijing, 2017, pp. 2851-2855. 10.1109/ICIP.2017.8296803

[4] Chopra, S., Hadsell. R. & LeCun, Y. (2005) Learning a Similarity Metric Discriminatively, With Application to Face Verification," 2005 IEEE Computer Society Conference on Computer Vision and Pattern Recognition (CVPR'05), San Diego, CA, USA, 2005, pp. 539-546 vol. 1. 10.1109/CVPR.2005.202

[5] Wen, Yandong & Zhang, Kaipeng & Li, Zhifeng & Qiao, Yu. (2016). A Discriminative Feature Learning Approach for Deep Face Recognition. LNCS. 9911. 499-515. 10.1007/978-3-319-46478-7_31. 